In [1]:
import numpy as np 
import pandas as pd 
from datetime import date

In [2]:
ratios = [0,0.236, 0.382, 0.5 , 0.618, 0.786,1,1.414,1.618]
fiblevels = np.array(ratios)

In [37]:
def RSI(series, period=14):
    delta = series.diff().dropna()
    ups = delta * 0
    downs = ups.copy()
    ups[delta > 0] = delta[delta > 0]
    downs[delta < 0] = -delta[delta < 0]
    ups[ups.index[period-1]] = np.mean( ups[:period] ) #first value is sum of avg gains
    ups = ups.drop(ups.index[:(period-1)])
    downs[downs.index[period-1]] = np.mean( downs[:period] ) #first value is sum of avg losses
    downs = downs.drop(downs.index[:(period-1)])
    rs = ups.ewm(com=period-1,min_periods=0,adjust=False,ignore_na=False).mean() / \
         downs.ewm(com=period-1,min_periods=0,adjust=False,ignore_na=False).mean() 
    return 100 - 100 / (1 + rs)


# calculating Stoch RSI (gives the same values as TradingView)
# https://www.tradingview.com/wiki/Stochastic_RSI_(STOCH_RSI) 
def STRSIA(series, period=14, smoothK=3, smoothD=3):
    # Calculate RSI 
    delta = series.diff().dropna()
    ups = delta * 0
    downs = ups.copy()
    ups[delta > 0] = delta[delta > 0]
    downs[delta < 0] = -delta[delta < 0]
    ups[ups.index[period-1]] = np.mean( ups[:period] ) #first value is sum of avg gains
    ups = ups.drop(ups.index[:(period-1)])
    downs[downs.index[period-1]] = np.mean( downs[:period] ) #first value is sum of avg losses
    downs = downs.drop(downs.index[:(period-1)])
    rs = ups.ewm(com=period-1,min_periods=0,adjust=False,ignore_na=False).mean() / \
         downs.ewm(com=period-1,min_periods=0,adjust=False,ignore_na=False).mean() 
    rsi = 100 - 100 / (1 + rs)

    # Calculate StochRSI 
    stochrsi  = (rsi - rsi.rolling(period).min()) / (rsi.rolling(period).max() - rsi.rolling(period).min())
    stochrsi_K = stochrsi.rolling(smoothK).mean()
    stochrsi_D = stochrsi_K.rolling(smoothD).mean()
    return stochrsi, stochrsi_K, stochrsi_D

In [38]:
ratios

[0, 0.236, 0.382, 0.5, 0.618, 0.786, 1, 1.414, 1.618]

In [150]:
ada15 = pd.read_json('BN-main/ADA_USDT-1h.json')
ada15

0        1        2        3        4            5
0      1546300800000  0.04057  0.04059  0.03995  0.04035   5902479.60
1      1546304400000  0.04040  0.04048  0.03987  0.04000   3739370.50
2      1546308000000  0.04004  0.04004  0.03964  0.03991   3615775.00
3      1546311600000  0.03988  0.04021  0.03985  0.04020   2419828.60
4      1546315200000  0.04020  0.04068  0.04017  0.04043   5649221.70
...              ...      ...      ...      ...      ...          ...
22152  1626235200000  1.21680  1.23060  1.21220  1.22100   7593028.91
22153  1626238800000  1.22080  1.22170  1.19800  1.20280  15978748.32
22154  1626242400000  1.20280  1.22000  1.19980  1.20740   7789568.81
22155  1626246000000  1.20750  1.22410  1.20660  1.22200   6168385.93
22156  1626249600000  1.22180  1.22500  1.20890  1.21020   4919397.66

[22157 rows x 6 columns]

In [151]:
ada15.columns=['date','open','high','low','close','volume']
ada15

date     open     high      low    close       volume
0      1546300800000  0.04057  0.04059  0.03995  0.04035   5902479.60
1      1546304400000  0.04040  0.04048  0.03987  0.04000   3739370.50
2      1546308000000  0.04004  0.04004  0.03964  0.03991   3615775.00
3      1546311600000  0.03988  0.04021  0.03985  0.04020   2419828.60
4      1546315200000  0.04020  0.04068  0.04017  0.04043   5649221.70
...              ...      ...      ...      ...      ...          ...
22152  1626235200000  1.21680  1.23060  1.21220  1.22100   7593028.91
22153  1626238800000  1.22080  1.22170  1.19800  1.20280  15978748.32
22154  1626242400000  1.20280  1.22000  1.19980  1.20740   7789568.81
22155  1626246000000  1.20750  1.22410  1.20660  1.22200   6168385.93
22156  1626249600000  1.22180  1.22500  1.20890  1.21020   4919397.66

[22157 rows x 6 columns]

In [152]:
start = pd.to_datetime('2020-01-01')
ada15.date=pd.to_datetime(ada15['date'],unit='ms')
ada15


date     open     high      low    close       volume
0     2019-01-01 00:00:00  0.04057  0.04059  0.03995  0.04035   5902479.60
1     2019-01-01 01:00:00  0.04040  0.04048  0.03987  0.04000   3739370.50
2     2019-01-01 02:00:00  0.04004  0.04004  0.03964  0.03991   3615775.00
3     2019-01-01 03:00:00  0.03988  0.04021  0.03985  0.04020   2419828.60
4     2019-01-01 04:00:00  0.04020  0.04068  0.04017  0.04043   5649221.70
...                   ...      ...      ...      ...      ...          ...
22152 2021-07-14 04:00:00  1.21680  1.23060  1.21220  1.22100   7593028.91
22153 2021-07-14 05:00:00  1.22080  1.22170  1.19800  1.20280  15978748.32
22154 2021-07-14 06:00:00  1.20280  1.22000  1.19980  1.20740   7789568.81
22155 2021-07-14 07:00:00  1.20750  1.22410  1.20660  1.22200   6168385.93
22156 2021-07-14 08:00:00  1.22180  1.22500  1.20890  1.21020   4919397.66

[22157 rows x 6 columns]

In [153]:
start = pd.to_datetime('2021-01-01')
end = pd.to_datetime('2021-04-20')

## adjust the timeperiods fro 15 x 4 or it will be 15min 1 hour and 2 hours 

ada2021 = ada15.loc[(ada15['date']> start)& (ada15['date']< end)].copy()
ada2021['RSI'] = RSI(ada2021['close'])
ada2021['RSI4']=RSI(ada2021['close'],56)
ada2021['RSI8']=RSI(ada2021['close'],112)

ada2021['STRSI'] = STRSIA(ada2021['close'])[0]
ada2021['STRSIK'] = STRSIA(ada2021['close'])[1]
ada2021['STRSID'] = STRSIA(ada2021['close'])[2]
ada2021['ABST1'] = abs(abs(ada2021['STRSIK']) - abs(ada2021['STRSID']))

ada2021['STRSI4'] = STRSIA(ada2021['close'],56,12,12)[0]
ada2021['STRSIK4'] = STRSIA(ada2021['close'],56,12,12)[1]
ada2021['STRSID4'] = STRSIA(ada2021['close'],56,12,12)[2]
ada2021['ABST4'] = abs(abs(ada2021['STRSIK4']) - abs(ada2021['STRSID4']))


ada2021['STRSI8'] = STRSIA(ada2021['close'],112,24,24)[0]
ada2021['STRSIK8'] = STRSIA(ada2021['close'],112,24,24)[1]
ada2021['STRSID8'] = STRSIA(ada2021['close'],112,24,24)[2]
ada2021['ABST8'] = abs(abs(ada2021['STRSIK8']) - abs(ada2021['STRSID8']))




ada2021

date     open     high      low    close      volume  \
17500 2021-01-01 01:00:00  0.18055  0.18469  0.18000  0.18358  28601648.4   
17501 2021-01-01 02:00:00  0.18361  0.18473  0.18229  0.18368  20075571.1   
17502 2021-01-01 03:00:00  0.18375  0.18458  0.18259  0.18292  15704497.1   
17503 2021-01-01 04:00:00  0.18299  0.18367  0.18105  0.18180  16338316.2   
17504 2021-01-01 05:00:00  0.18182  0.18339  0.18171  0.18297   9273656.6   
...                   ...      ...      ...      ...      ...         ...   
20108 2021-04-19 19:00:00  1.22626  1.24044  1.21268  1.23000  15518405.4   
20109 2021-04-19 20:00:00  1.23000  1.24130  1.22158  1.23574   9430654.3   
20110 2021-04-19 21:00:00  1.23571  1.24500  1.21509  1.22826  12297314.7   
20111 2021-04-19 22:00:00  1.22861  1.23035  1.20871  1.21259  11078989.7   
20112 2021-04-19 23:00:00  1.21282  1.22215  1.19121  1.19450  14946859.8   

             RSI       RSI4       RSI8     STRSI  ...    STRSID     ABST1  \
17500        NaN        NaN        NaN       NaN  ...       NaN       NaN   
17501        NaN        NaN        NaN       NaN  ...       NaN       NaN   
17502        NaN        NaN        NaN       NaN  ...       NaN       NaN   
17503        NaN        NaN        NaN       NaN  ...       NaN       NaN   
17504        NaN        NaN        NaN       NaN  ...       NaN       NaN   
...          ...        ...        ...       ...  ...       ...       ...   
20108  45.610208  45.411558  47.338609  0.548533  ...  0.312864  0.164551   
20109  46.883313  45.736024  47.513543  0.611484  ...  0.450433  0.107322   
20110  45.392227  45.378149  47.306914  0.801662  ...  0.563021  0.090872   
20111  42.353278  44.633205  46.876003  0.577654  ...  0.625083  0.038517   
20112  39.098950  43.788259  46.383857  0.337770  ...  0.629952  0.057590   

         STRSI4   STRSIK4   STRSID4     ABST4    STRSI8   STRSIK8   STRSID8  \
17500       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
17501       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
17502       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
17503       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
17504       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
...         ...       ...       ...       ...       ...       ...       ...   
20108  0.638789  0.516733  0.586541  0.069808  0.286672  0.322382  0.236469   
20109  0.670564  0.524331  0.576104  0.051773  0.300425  0.323611  0.245844   
20110  0.649511  0.534397  0.566747  0.032350  0.284180  0.324349  0.254949   
20111  0.588644  0.545431  0.559558  0.014127  0.250303  0.321561  0.263519   
20112  0.519606  0.539536  0.551815  0.012279  0.211611  0.318029  0.271430   

          ABST8  
17500       NaN  
17501       NaN  
17502       NaN  
17503       NaN  
17504       NaN  
...         ...  
20108  0.085913  
20109  0.077768  
20110  0.069400  
20111  0.058042  
20112  0.046598  

[2613 rows x 21 columns]

In [154]:
#maxlevels = [13,13,13,13,13,13,13]
#maxlevels = np.array(maxlevels)
#maxlevels

In [155]:
#minlevels = [11,11,11,11,11,11,11]
#minlevels = np.array(minlevels)
#minlevels

In [156]:
ada2021

date     open     high      low    close      volume  \
17500 2021-01-01 01:00:00  0.18055  0.18469  0.18000  0.18358  28601648.4   
17501 2021-01-01 02:00:00  0.18361  0.18473  0.18229  0.18368  20075571.1   
17502 2021-01-01 03:00:00  0.18375  0.18458  0.18259  0.18292  15704497.1   
17503 2021-01-01 04:00:00  0.18299  0.18367  0.18105  0.18180  16338316.2   
17504 2021-01-01 05:00:00  0.18182  0.18339  0.18171  0.18297   9273656.6   
...                   ...      ...      ...      ...      ...         ...   
20108 2021-04-19 19:00:00  1.22626  1.24044  1.21268  1.23000  15518405.4   
20109 2021-04-19 20:00:00  1.23000  1.24130  1.22158  1.23574   9430654.3   
20110 2021-04-19 21:00:00  1.23571  1.24500  1.21509  1.22826  12297314.7   
20111 2021-04-19 22:00:00  1.22861  1.23035  1.20871  1.21259  11078989.7   
20112 2021-04-19 23:00:00  1.21282  1.22215  1.19121  1.19450  14946859.8   

             RSI       RSI4       RSI8     STRSI  ...    STRSID     ABST1  \
17500        NaN        NaN        NaN       NaN  ...       NaN       NaN   
17501        NaN        NaN        NaN       NaN  ...       NaN       NaN   
17502        NaN        NaN        NaN       NaN  ...       NaN       NaN   
17503        NaN        NaN        NaN       NaN  ...       NaN       NaN   
17504        NaN        NaN        NaN       NaN  ...       NaN       NaN   
...          ...        ...        ...       ...  ...       ...       ...   
20108  45.610208  45.411558  47.338609  0.548533  ...  0.312864  0.164551   
20109  46.883313  45.736024  47.513543  0.611484  ...  0.450433  0.107322   
20110  45.392227  45.378149  47.306914  0.801662  ...  0.563021  0.090872   
20111  42.353278  44.633205  46.876003  0.577654  ...  0.625083  0.038517   
20112  39.098950  43.788259  46.383857  0.337770  ...  0.629952  0.057590   

         STRSI4   STRSIK4   STRSID4     ABST4    STRSI8   STRSIK8   STRSID8  \
17500       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
17501       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
17502       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
17503       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
17504       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
...         ...       ...       ...       ...       ...       ...       ...   
20108  0.638789  0.516733  0.586541  0.069808  0.286672  0.322382  0.236469   
20109  0.670564  0.524331  0.576104  0.051773  0.300425  0.323611  0.245844   
20110  0.649511  0.534397  0.566747  0.032350  0.284180  0.324349  0.254949   
20111  0.588644  0.545431  0.559558  0.014127  0.250303  0.321561  0.263519   
20112  0.519606  0.539536  0.551815  0.012279  0.211611  0.318029  0.271430   

          ABST8  
17500       NaN  
17501       NaN  
17502       NaN  
17503       NaN  
17504       NaN  
...         ...  
20108  0.085913  
20109  0.077768  
20110  0.069400  
20111  0.058042  
20112  0.046598  

[2613 rows x 21 columns]

In [157]:
high = ada2021.high
low = ada2021.low
maximums5 = high.rolling(5,5)
max5 = maximums5.max()
minimums5 = low.rolling(5,5)
min5 = minimums5.min()
maximums10 = high.rolling(10,10)
max10 = maximums10.max()
minimums10 = low.rolling(10,10)
min10 = minimums10.min()


In [158]:
len(max5)

2613

In [159]:

ada2021['max5'] = max5
ada2021['max10'] = max10
ada2021['min5'] = min5
ada2021['min10'] = min10

ada2021.tail()

date     open     high      low    close      volume  \
20108 2021-04-19 19:00:00  1.22626  1.24044  1.21268  1.23000  15518405.4   
20109 2021-04-19 20:00:00  1.23000  1.24130  1.22158  1.23574   9430654.3   
20110 2021-04-19 21:00:00  1.23571  1.24500  1.21509  1.22826  12297314.7   
20111 2021-04-19 22:00:00  1.22861  1.23035  1.20871  1.21259  11078989.7   
20112 2021-04-19 23:00:00  1.21282  1.22215  1.19121  1.19450  14946859.8   

             RSI       RSI4       RSI8     STRSI  ...   STRSID4     ABST4  \
20108  45.610208  45.411558  47.338609  0.548533  ...  0.586541  0.069808   
20109  46.883313  45.736024  47.513543  0.611484  ...  0.576104  0.051773   
20110  45.392227  45.378149  47.306914  0.801662  ...  0.566747  0.032350   
20111  42.353278  44.633205  46.876003  0.577654  ...  0.559558  0.014127   
20112  39.098950  43.788259  46.383857  0.337770  ...  0.551815  0.012279   

         STRSI8   STRSIK8   STRSID8     ABST8     max5    max10     min5  \
20108  0.286672  0.322382  0.236469  0.085913  1.24044  1.27304  1.17122   
20109  0.300425  0.323611  0.245844  0.077768  1.24130  1.27304  1.17150   
20110  0.284180  0.324349  0.254949  0.069400  1.24500  1.26972  1.18059   
20111  0.250303  0.321561  0.263519  0.058042  1.24500  1.26081  1.20871   
20112  0.211611  0.318029  0.271430  0.046598  1.24500  1.25438  1.19121   

         min10  
20108  1.17122  
20109  1.17122  
20110  1.17122  
20111  1.17122  
20112  1.17122  

[5 rows x 25 columns]

In [160]:
#maxnew = np.ones_like(ratios)
#maxnew

In [161]:
#addmin = mintest.tolist()
#addmax = maxtest.tolist()
#data = pd.DataFrame({"max":maxtest,"min":mintest},dtype='float')
#data = data.append(addmin,ignore_index=True)
#data1 = pd.DataFrame(maxtest)
#data2 = pd.DataFrame(mintest)
#data = pd.DataFrame(data1,data2)

In [163]:
#datamul = data.mul([2,1],axis='columns')
#datamul = data['max'].mul(ratios[7])

In [164]:
#datamul

In [165]:
#df = ada2021.loc[(ada2021['max10']>0)& (ada2021['min10']>0)]
df = ada2021
#len(df['date'])
average = df['max5']-df['min5']
avg = average.mean()
avg
df
#point = df.loc[(df['max5'].diff()>0)]
#pointm = df.loc[(df['min5'].diff()>0)]

df['support5']= df.min5.rolling(5,5).min()
df['support10']= df.min10.rolling(10,10).min()
df['resist5']= df.max5.rolling(5,5).max()
df['resist10']= df.max10.rolling(10,10).max()

#df['RSI'] = RSI(df['close'])
#df['STRSI4']=STRSIA(df['close'],56,12,12)
#df['STRSI8']=STRSIA(df['close'],112,24,24)


point = df[(df['max5'] > df['max5'].shift(1)) &  (df['max5'].shift(1) > df['max5'].shift(2))]
pointm = df[(df['min5'] < df['min5'].shift(1)) &  (df['min5'].shift(1) > df['min5'].shift(2))]
point
#ada2021
test =df.loc[df['STRSI'] < 0.2]
test

#for row in range(0,len(pointm)):
#    print(pointm['support5'])

date     open     high      low    close      volume  \
17548 2021-01-03 01:00:00  0.17646  0.17700  0.17410  0.17578  22602251.2   
17549 2021-01-03 02:00:00  0.17578  0.17578  0.17432  0.17494  13452605.3   
17550 2021-01-03 03:00:00  0.17494  0.17512  0.17392  0.17446   9862448.4   
17552 2021-01-03 05:00:00  0.17572  0.17693  0.17407  0.17472  23537143.5   
17554 2021-01-03 07:00:00  0.17664  0.17665  0.17407  0.17436  21234047.7   
...                   ...      ...      ...      ...      ...         ...   
20099 2021-04-19 10:00:00  1.25724  1.26035  1.20590  1.23361  32678917.6   
20101 2021-04-19 12:00:00  1.26943  1.26972  1.23771  1.24305  16440535.2   
20103 2021-04-19 14:00:00  1.25438  1.25438  1.17916  1.20889  40915632.4   
20104 2021-04-19 15:00:00  1.20885  1.21540  1.17122  1.18041  44108144.1   
20105 2021-04-19 16:00:00  1.18046  1.21654  1.17150  1.18705  30833436.9   

             RSI       RSI4       RSI8     STRSI  ...   STRSID8     ABST8  \
17548  45.621023        NaN        NaN  0.160954  ...       NaN       NaN   
17549  43.870876        NaN        NaN  0.086950  ...       NaN       NaN   
17550  42.859066        NaN        NaN  0.044165  ...       NaN       NaN   
17552  44.121475        NaN        NaN  0.097546  ...       NaN       NaN   
17554  44.076625        NaN        NaN  0.098306  ...       NaN       NaN   
...          ...        ...        ...       ...  ...       ...       ...   
20099  39.435613  44.501759  47.106251  0.000000  ...  0.144725  0.136406   
20101  43.191897  45.308054  47.477353  0.191644  ...  0.165288  0.138359   
20103  38.302687  43.837883  46.573829  0.000000  ...  0.186725  0.128121   
20104  34.516690  42.587876  45.816125  0.000000  ...  0.197082  0.116711   
20105  36.102488  42.973879  46.022707  0.064676  ...  0.207151  0.106183   

          max5    max10     min5    min10  support5  support10  resist5  \
17548  0.17924  0.18457  0.17050  0.17050   0.17050    0.16793  0.18457   
17549  0.17924  0.18457  0.17410  0.17050   0.17050    0.16793  0.18457   
17550  0.17917  0.18457  0.17392  0.17050   0.17050    0.16793  0.18457   
17552  0.17700  0.18383  0.17358  0.17050   0.17050    0.17026  0.17924   
17554  0.17725  0.17924  0.17358  0.17358   0.17358    0.17050  0.17917   
...        ...      ...      ...      ...       ...        ...      ...   
20099  1.30646  1.32443  1.20590  1.20590   1.20590    1.20590  1.32443   
20101  1.30646  1.32443  1.20590  1.20590   1.20590    1.20590  1.32370   
20103  1.27304  1.30646  1.17916  1.17916   1.17916    1.17916  1.30646   
20104  1.27304  1.30646  1.17122  1.17122   1.17122    1.17122  1.30646   
20105  1.26972  1.30646  1.17122  1.17122   1.17122    1.17122  1.30646   

       resist10  
17548   0.18457  
17549   0.18457  
17550   0.18457  
17552   0.18457  
17554   0.18457  
...         ...  
20099   1.32443  
20101   1.32443  
20103   1.32443  
20104   1.32443  
20105   1.32443  

[715 rows x 29 columns]

In [166]:
import plotly.graph_objs as go
from plotly.subplots import make_subplots


#Declare figure


fig = go.Figure()

fig = make_subplots(rows=9, cols=1,subplot_titles=("Price","gap","empty", "RSI 1 4 8", "Stoch 1", "Stoch 4","Stoch 8","Stoch 1 4 8","Abs Stoch"))
    

fig.add_trace(
    go.Scatter(x=df.date, y=df['RSI'],
        name="RSI",
        text="RSI",
        textposition="top center"),
    row=4, col=1
)

fig.add_trace(
    go.Scatter(x=df.date, y=df['RSI4'],name="RSI4"),
    row=4, col=1
)

fig.add_trace(
    go.Scatter(x=df.date, y=df['RSI8'],name="RSI8"),
    row=4, col=1
)

fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI'],name="STRSI"),
    row=5, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSIK'],name="STRSIK"),
    row=5, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSID'],name="STRSID"),
    row=5, col=1
)
    
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI4'],name="STRSI4"),
    row=6, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSIK4'],name="STRSIK4"),
    row=6, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSID4'],name="STRSID4"),
    row=6, col=1
)
    
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI8'],name="STRSI8"),
    row=7, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSIK8'],name="STRSIK8"),
    row=7, col=1
)

fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSID8'],name="STRSIK8"),
    row=7, col=1
)


fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI8'],name="STRSI8"),
    row=8, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI4'],name="STRSI4"),
    row=8, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI'],name="STRSI"),
    row=8, col=1
)


fig.add_trace(
    go.Scatter(x=df.date, y=df['ABST1'],name="ABST1"),
    row=9, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['ABST4'],name="ABST4"),
    row=9, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['ABST8'],name="ABST8"),
    row=9, col=1
)



#add Traces

fig.add_trace(go.Candlestick(x=df.date,
                open=df['open'],
                high=df['high'],
                low=df['low'],
                close=df['close'], name = 'market data'),row=1,col=1)

#fig.add_trace(go.Scatter(x=df['date'], y=df['max10']))

#fig.add_trace(go.Scatter(x=df['date'], y=df['min10']))

#fig.add_trace(go.Scatter(x=point['date'], y=point['resist5']))

#fig.add_trace(go.Scatter(x=pointm['date'], y=pointm['support5']))


#fig.add_shape(type="line",
#    x0=pointm['date'], y0=pointm['support5'], x1=max(pointm['date']), y1=pointm['support5'],
#    line=dict(
#        color="LightSeaGreen",
#        width=4,
#        dash="dashdot",
#    ))
fig.update_shapes(dict(xref='x', yref='y'))

#for index in range(0,len(pointm)):
    #fig.add_hline(y=pointm['support5'])

#fig.add_trace(go.Scatter(x=point['date'], y=point['resist10']))

#fig.add_trace(go.Scatter(x=pointm['date'], y=pointm['support10']))
#for i in range(len(df['date'])):
    #fig.add_hline(y=df[i]['min10'], line_dash="dot",
                  #annotation_text="support", 
                  #annotation_position="bottom right")

#fig.add_hline(y=df['max10'], line_dash="dot",
#              annotation_text="resitance", 
#              annotation_position="bottom right")



fig.update_layout(height=3000, width=800, title_text="top sub plots")
# X and Y Axis Update
fig.update_xaxes(
    title = 'Date',rangeslider_visible=False
)

#fig.update_yaxes(
#    title = 'Share Price (USD)'
#)

#Show
fig.show()